# Introduction

Main notebook for trying out code fragments, or unit different modules.  Similar to def main().

## Data preprocessing

Various code fragments to process the Kaggle dataset.  The full Kaggle data must be stored locally.  Functions are stored in some external python scripts which are also stored locally (e.g. final_project/*).

In [123]:
import pandas as pd
import numpy as np
import json
import tensorflow as tf
from tqdm import tqdm

In [124]:
def random_sample_negative_candidates(distribution):
    temp = np.random.random()
    value = 0.
    for index in range(len(distribution)):
        value += distribution[index]
        if value > temp:
            break
    return index

def inputdata_KaggleWinner(json_dir, max_data = 9999999999):
    # prepare input
    #json_dir = '../../input/simplified-nq-train.jsonl'
    #max_data = 9999999999

    id_list = []
    data_dict = {}
    with open(json_dir) as f:
        for n, line in tqdm(enumerate(f)):
            if n > max_data:
                break
            data = json.loads(line)

            is_pos = False
            annotations = data['annotations'][0]
            if annotations['yes_no_answer'] == 'YES':
                is_pos = True
            elif annotations['yes_no_answer'] == 'NO':
                is_pos = True
            elif annotations['short_answers']:
                is_pos = True
            elif annotations['long_answer']['candidate_index'] != -1:
                is_pos = True

            if is_pos and len(data['long_answer_candidates']) > 1:
                data_id = data['example_id']
                id_list.append(data_id)

                # uniform sampling
                distribution = np.ones((len(data['long_answer_candidates']),), dtype=np.float32)
                if is_pos:
                    distribution[data['annotations'][0]['long_answer']['candidate_index']] = 0.
                distribution /= len(distribution)
                negative_candidate_index = random_sample_negative_candidates(distribution)

                #
                doc_words = data['document_text'].split()
                # negative
                candidate = data['long_answer_candidates'][negative_candidate_index]
                negative_candidate_words = doc_words[candidate['start_token']:candidate['end_token']]
                negative_candidate_start = candidate['start_token']
                negative_candidate_end = candidate['end_token']
                # positive
                candidate = data['long_answer_candidates'][annotations['long_answer']['candidate_index']]
                positive_candidate_words = doc_words[candidate['start_token']:candidate['end_token']]
                positive_candidate_start = candidate['start_token']
                positive_candidate_end = candidate['end_token']

                print('data annots' , data['annotations'])
                # initialize data_dict
                data_dict[data_id] = {
                    'question_text': data['question_text'],
                    'annotations': data['annotations'],
                    'positive_text': positive_candidate_words,
                    'positive_start': positive_candidate_start,
                    'positive_end': positive_candidate_end,
                    'negative_text': negative_candidate_words,
                    'negative_start': negative_candidate_start,
                    'negative_end': negative_candidate_end,
                }

    return data_dict

def compute_statistics(datasetKaggle):
    """
    Outputs various statistics of the Kaggle dataset

    :param datasetKaggle: the input dataset formatted as a dictionary
    :type datasetKaggle: dict
    :return: dictionary with the processed information
    :rtype: dict


    """
    print('compute_statistics called')
    yesNoAnswer = 0
    annotationsMax = 0
    totalLength = 0
    totalExamples = len(datasetKaggle)

    i=0
    #print('datasetKaggle=',datasetKaggle)
    for example in datasetKaggle:
        #print('example:', i);
        #print(example)
        print('value part')
        print(example['annotations'])
        annotationsMax = max(len(example['annotations']), annotationsMax)  # check for the maximum number of annotations
        if example['annotations'][0]['yes_no_answer'] != 'NONE':
            yesNoAnswer += 1

        totalLength += len(example['document_text']) 
    averageLength = totalLength / totalExamples
    output = {'annotationsMax': annotationsMax, 'num_yesNo': yesNoAnswer, 'text_avgLength': averageLength}
    i = i + 1
    return output


In [121]:
json_dir = 'cs230_spring2020/final_project/simplified-nq-train.jsonl.full'
num_entries = 5000

dataset_kaggle = inputdata_KaggleWinner(json_dir, num_entries)

len(dataset_kaggle)

dataset_kaggle

271it [00:00, 1359.36it/s]

data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 1952, 'candidate_index': 54, 'end_token': 2019}, 'short_answers': [{'start_token': 1960, 'end_token': 1969}], 'annotation_id': 593165450220027640}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 212, 'candidate_index': 15, 'end_token': 310}, 'short_answers': [{'start_token': 213, 'end_token': 215}], 'annotation_id': 12034874153783787365}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 319, 'candidate_index': 24, 'end_token': 438}, 'short_answers': [], 'annotation_id': 10527123009892725162}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 509, 'candidate_index': 59, 'end_token': 576}, 'short_answers': [{'start_token': 512, 'end_token': 514}], 'annotation_id': 14634796365152556576}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 82, 'candidate_index': 7, 'end_token': 169}, 'short_answers': [{'start_token': 83, 'end_token': 85}], 

561it [00:00, 1403.95it/s]

data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 1618, 'candidate_index': 73, 'end_token': 1813}, 'short_answers': [{'start_token': 1673, 'end_token': 1674}], 'annotation_id': 18317396663960143170}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 53, 'candidate_index': 0, 'end_token': 230}, 'short_answers': [], 'annotation_id': 8394227903812414210}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 540, 'candidate_index': 18, 'end_token': 641}, 'short_answers': [{'start_token': 562, 'end_token': 567}], 'annotation_id': 2519173687451435589}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 185, 'candidate_index': 11, 'end_token': 334}, 'short_answers': [], 'annotation_id': 14240855338080410049}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 638, 'candidate_index': 4, 'end_token': 750}, 'short_answers': [{'start_token': 684, 'end_token': 685}], 'annotation_id': 11915006256841949820

817it [00:00, 1332.12it/s]

...

4927it [00:03, 1350.64it/s]

data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 425, 'candidate_index': 41, 'end_token': 503}, 'short_answers': [{'start_token': 450, 'end_token': 452}], 'annotation_id': 3510021150369975071}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 793, 'candidate_index': 69, 'end_token': 974}, 'short_answers': [{'start_token': 867, 'end_token': 868}], 'annotation_id': 1573610838878712038}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 183, 'candidate_index': 15, 'end_token': 225}, 'short_answers': [{'start_token': 184, 'end_token': 186}], 'annotation_id': 3791314156069538645}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 79, 'candidate_index': 0, 'end_token': 331}, 'short_answers': [{'start_token': 130, 'end_token': 131}], 'annotation_id': 2350292552701851392}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 36, 'candidate_index': 0, 'end_token': 186}, 'short_answers': [{'start_t

5001it [00:03, 1287.54it/s]


data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 123, 'candidate_index': 11, 'end_token': 260}, 'short_answers': [{'start_token': 247, 'end_token': 248}], 'annotation_id': 614297059522215212}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 109, 'candidate_index': 3, 'end_token': 246}, 'short_answers': [{'start_token': 136, 'end_token': 138}], 'annotation_id': 927393246966995434}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 6564, 'candidate_index': 228, 'end_token': 6659}, 'short_answers': [], 'annotation_id': 12904186001711505878}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 221, 'candidate_index': 20, 'end_token': 267}, 'short_answers': [{'start_token': 238, 'end_token': 241}], 'annotation_id': 12125728296553915539}]
data annots [{'yes_no_answer': 'NONE', 'long_answer': {'start_token': 12098, 'candidate_index': 211, 'end_token': 12323}, 'short_answers': [{'start_token': 12122, 'end_token': 

{5655493461695504401: {'annotations': [{'annotation_id': 593165450220027640,
    'long_answer': {'candidate_index': 54,
     'end_token': 2019,
     'start_token': 1952},
    'short_answers': [{'end_token': 1969, 'start_token': 1960}],
    'yes_no_answer': 'NONE'}],
  'negative_end': 1792,
  'negative_start': 1730,
  'negative_text': ['<P>',
   'Companies',
   'considering',
   'the',
   'use',
   'of',
   'an',
   'email',
   'marketing',
   'program',
   'must',
   'make',
   'sure',
   'that',
   'their',
   'program',
   'does',
   'not',
   'violate',
   'spam',
   'laws',
   'such',
   'as',
   'the',
   'United',
   'States',
   "'",
   'Controlling',
   'the',
   'Assault',
   'of',
   'Non-Solicited',
   'Pornography',
   'and',
   'Marketing',
   'Act',
   '(',
   'CAN',
   '-',
   'SPAM',
   ')',
   ',',
   'the',
   'European',
   'Privacy',
   'and',
   'Electronic',
   'Communications',
   'Regulations',
   '2003',
   ',',
   'or',
   'their',
   'Internet',
   'service',

In [122]:
dataset_kaggle_statistics = compute_statistics(dataset_kaggle)

print(dataset_kaggle_statistics)

compute_statistics called
value part


TypeError: 'int' object is not subscriptable

Code to product an extract of the Kaggle set data